# Fine-tuning du modèle

In [ ]:
!pip install ultralytics

In [5]:
from ultralytics import YOLO
import torch

device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(f"Accélerateur utilisé: {device}")

Accélerateur utilisé: cuda


In [6]:
# Arguments d'apprentissage principaux
# Infos supplémentaires: https://docs.ultralytics.com/modes/train/
train_args = {
        'data': 'coco8-pose.yaml',  # Spécifier votre fichier de configuration de dataset ici
        # Pour plus de détails sur le format de datasets, voir:
        #   - Détection d'objets: https://docs.ultralytics.com/datasets/detect/
        #   - Estimation de pose: https://docs.ultralytics.com/datasets/pose/

        'imgsz': 640,  # Taille des images (peut recevoir un tuple (Hauteur, Largeur), sinon les images sont ajustés en carrés)
        'project': 'runs/pose',     # Repertoire du modèle
        'name': 'yolo_finetune',    # Nom du nouveau modèle
        'exist_ok': True,           # Ecrase l'itération précédente du projet si elle existe déjà


        'resume': False,   # Reprendre l'apprentissage à partir d'un checkpoint récent
        'pretrained': True, # Reprendre des poids de modèle pré-entrainés

        'epochs': 50,  # Nombre d'époques pour l'apprentissage
        'patience': 10,  # Nombre d'époques avant le early stopping (arrêter lorsque le modèle ne s'améliore plus pendant trop longtemps)

        'batch': 16,  # Taille de batchs à traiter en parallèle

        'optimizer': 'AdamW',  # Optimiseur à utiliser (SGD, Adam ou AdamW)
        'weight_decay': 0.0005,  # Régularisation L2 (évite l'overfitting)
        'lr0': 0.001,  # Learning rate initial pour l'optimiseur
        'lrf': 0.1,    # Learning rate final en tant que fraction du lr initial

        'val': True,       # Valider automatiquement à chaque époque
        'save': True,      # Enregistrer des checkpoints intermédiaires
        'save_period': 10, # Enregistrer tous les N époques
        'plots': True,     # Enregistrer des graphiques d'apprentissage
        'device': device,  # GPU à utiliser

        'freeze': None,    # Geler les couches du modèle (évite de les modifier lors de l'apprentissage)
        'dropout': 0.0,    # Probabilitéi de dropout (évite l'overfitting)
}

In [7]:
# Arguments d'augmentation de données, permet d'ajuster le dataset lors de l'apprentissage
# pour endre le modèle plus robuste et empêche l'overfitting
# Infos supplémentaires: https://docs.ultralytics.com/guides/yolo-data-augmentation/
data_augmentation_args = {
        'augment': True,  # Active l'augmentation
        'hsv_h': 0.015,    # Fait varier la teinte de l'image ("Hue" dans HSV)
        'hsv_s': 0.7,      # Fait varier la saturation de l'image ("Saturation" dans HSV)
        'hsv_v': 0.4,      # Fait varier la luminosité de l'image ("Value" dans HSV)
        'degrees': 10.0,   # Rotation de l'image maximale
        'translate': 0.1,  # Translation de l'image (proportionelle à la taille de l'image)
        'scale': 0.3,      # Mise à l'échelle de l'image, ie zoom (proportionel à la taille de l'image)
        'shear': 2.0,      # Transvection (fait pencher l'image de n degrés)
        'perspective': 0.0001,  # Ajustement de perspective
        'flipud': 0.0,     # Probabilité de retourner l'image verticalement
        'fliplr': 0.5,     # Probabilité de retourner l'image horizontalement
        'mosaic': 0.5,     # Probabilité de coller plusieurs images en une seule
        'mixup': 0.1,      # Probabilité de superposer une image par dessus une autre (voir https://docs.ultralytics.com/guides/yolo-data-augmentation/#mixup-mixup)
}

In [9]:
# Spécifier le modèle pré-entraineé à utiliser comme base ici
# Plus d'informations sur les différentes variantes de YOLOv11:
#   https://docs.ultralytics.com/models/yolo11/#supported-tasks-and-modes
yolo = YOLO('yolo11s-pose.pt')

print("\nInformations sur le modèle:")
print(f"Tâche du modèle: {yolo.task}")
print(f"Structure du modèle: {yolo}")


Informations sur le modèle:
Tâche du modèle: pose
Structure du modèle: YOLO(
  (model): PoseModel(
    (model): Sequential(
      (0): Conv(
        (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (bn): BatchNorm2d(32, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
        (act): SiLU(inplace=True)
      )
      (1): Conv(
        (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1), bias=False)
        (bn): BatchNorm2d(64, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
        (act): SiLU(inplace=True)
      )
      (2): C3k2(
        (cv1): Conv(
          (conv): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn): BatchNorm2d(64, eps=0.001, momentum=0.03, affine=True, track_running_stats=True)
          (act): SiLU(inplace=True)
        )
        (cv2): Conv(
          (conv): Conv2d(96, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn): B

In [10]:
# Fine-tuning du modèle avec les paramètres spécifiés

results = yolo.train(**(train_args|data_augmentation_args))

New https://pypi.org/project/ultralytics/8.3.143 available 😃 Update with 'pip install -U ultralytics'
Ultralytics 8.3.24 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: task=pose, mode=train, model=yolo11s-pose.pt, data=coco8-pose.yaml, epochs=50, time=None, patience=10, batch=16, imgsz=640, save=True, save_period=10, cache=False, device=cuda, workers=8, project=runs/pose, name=yolo_finetune, exist_ok=True, pretrained=True, optimizer=AdamW, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=True, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_fra

train: Scanning /content/datasets/coco8-pose/labels/train.cache... 4 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4/4 [00:00<?, ?it/s]

albumentations: Blur(p=0.01, blur_limit=(3, 7)), MedianBlur(p=0.01, blur_limit=(3, 7)), ToGray(p=0.01, method='weighted_average', num_output_channels=3), CLAHE(p=0.01, clip_limit=(1.0, 4.0), tile_grid_size=(8, 8))



/usr/local/lib/python3.11/dist-packages/ultralytics/data/augment.py:1850: UserWarning: Argument(s) 'quality_lower' are not valid for transform ImageCompression
  A.ImageCompression(quality_lower=75, p=0.0),
val: Scanning /content/datasets/coco8-pose/labels/val.cache... 4 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4/4 [00:00<?, ?it/s]


Plotting labels to runs/pose/yolo_finetune/labels.jpg... 
optimizer: AdamW(lr=0.001, momentum=0.937) with parameter groups 87 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
TensorBoard: model graph visualization added ✅
Image sizes 640 train, 640 val
Using 2 dataloader workers
Logging results to runs/pose/yolo_finetune
Starting training for 50 epochs...

      Epoch    GPU_mem   box_loss  pose_loss  kobj_loss   cls_loss   dfl_loss  Instances       Size


...


14 epochs completed in 0.007 hours.
Optimizer stripped from runs/pose/yolo_finetune/weights/last.pt, 20.2MB
Optimizer stripped from runs/pose/yolo_finetune/weights/best.pt, 20.2MB

Validating runs/pose/yolo_finetune/weights/best.pt...
Ultralytics 8.3.24 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
YOLO11s-pose summary (fused): 257 layers, 9,902,940 parameters, 0 gradients, 23.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Pose(P          R      mAP50  mAP50-95):   0%|          | 0/1 [00:00<?, ?it/s]

WARNING ⚠️ Model does not support 'augment=True', reverting to single-scale prediction.


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Pose(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00,  8.76it/s]


                   all          4         14      0.972      0.857      0.946      0.765      0.913      0.857      0.898      0.505
Speed: 0.3ms preprocess, 20.3ms inference, 0.0ms loss, 0.9ms postprocess per image
Results saved to runs/pose/yolo_finetune


In [ ]:
# Le output affiché par le procédé d'apprentissage d'ultralitics peut paraitre
# intimidant, de ce fait voici un bref explicatif des aspects les plus importants:
#
# À chaque époque le procédé affiche la progression de l'entrainement du modèle
#
# Epoch    GPU_mem   box_loss  pose_loss  kobj_loss   cls_loss   dfl_loss  Instances       Size
# 1/50      1.63G      2.086      1.529     0.3131      1.007      1.854         11        640: 100%|██████████| 1/1 [00:00<00:00,  3.83it/s]
#
#           Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Pose(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00,  7.28it/s]
#             all          4         14      0.946      0.857      0.942      0.757      0.912      0.857       0.87      0.496
#
# Dans l'exemple ci-dessus la première rangée concerne les perfomances du finetuning:
#    Les valeurs de divers termes de la fonction de coup de l'époque en cours:
#    box_loss, pose_loss, kobj_loss, cls_loss, dfl_loss
#
# La deuxième ligne concerne les performances de validation du modèle sur un
# sous-ensemble de validation dans le jeu de données d'apprentissage:
#    Box() : Performances pour la tâche de detection
#       P : Précision pour les boîtes englobantes
#           - Quelle fraction des boîtes englobantes prédites sont correctes ?
#       R : Rappel pour les boîtes englobantes
#           - Quelle fraction des boîtes englobantes corrects ont été détectées ?
#       mAP50 : Précision Moyenne Moyenne à IoU=0,5 (Intersection over Union)
#           - Précision moyenne de toutes les classes au seuil de chevauchement de 50%
#       mAP50-95 : Précision Moyenne Moyenne à IoU=0,5:0,95
#           - Précision moyenne sur les seuils IoU de 50% à 95% (métrique plus stricte)
#
#   Pose(): Performances pour la tâche d'estimation de pose
#       P : Précision pour les points-clés
#           - Quelle fraction des points-clés prédits sont corrects ?
#       R : Rappel pour les points-clés
#           - Quelle fraction des points-clés corrects ont été détectés ?
#       mAP50 : Précision Moyenne Moyenne pour les points-clés à OKS=0,5 (Object Keypoint Similarity)
#       mAP50-95 : Précision Moyenne Moyenne pour les points-clés across les seuils OKS de 0,5 à 0,95

In [ ]:
# Au vu du nombre très élevé d'hyperparamètres d'apprentissage différents
# il est copliqué d'identifier la configaration d'apprentissage optimale
#
# Ultralytics supporte la fonctionalité de tuning d'hyperparamètres qui permet
# d'automatiquement entrainer une série série de configurations différentes et
# séléctionner la meilleure. Des informations supplémentaires sont disponibles
# au lien suivant: https://docs.ultralytics.com/guides/hyperparameter-tuning/
#
# Note: le tuning éffectue un très grand nombre de procédés d'apprentissages,
# de ce fait pensez à réduire le nombre d'époques afin de rester dans les délais

# Distillation de conaissances

In [15]:
# La distillation de conaissances est uniquement disponible dans un fork du projet
# ultralytics, pour l'installation suivez les instructions du lien suivant:
# https://github.com/danielsyahputra/yolo-distiller

# Ci-dessous voici les instructions qui fonctionnent dans Google Colab
# Attention: nécéssitera le redémarrage de la session actuelle
!git clone https://github.com/danielsyahputra/yolo-distiller
!pip install ./yolo-distiller/

fatal: destination path 'yolo-distiller' already exists and is not an empty directory.
Processing ./yolo-distiller
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for ultralytics: filename=ultralytics-8.3.24-py3-none-any.whl size=855357 sha256=2d923e2230d3ecf51d28d27404026a05a35946471249500c01d705ea5c3920de
  Stored in directory: /root/.cache/pip/wheels/94/5e/5d/e2af9429c9b9a94d1d2237e944f17c7fb40dd25b8805d91ea3
Successfully built ultralytics
  Attempting uninstall: ultralytics
    Found existing installation: ultralytics 8.3.24
    Uninstalling ultralytics-8.3.24:
      Successfully uninstalled ultralytics-8.3.24


In [2]:
from ultralytics import YOLO

teacher_model = YOLO('yolo11l.pt')
student_model = YOLO('yolo11s.pt')

distillation_args = {
    'teacher': teacher_model.model, # Le modèle enseignant (généralement beaucoup plus gros que le modèle étudiant)
    'distillation_loss': "cwd",  # Type de fonction de perte à utiliser lors de la distillation

    'name': 'yolo_distillation', # Nom du nouveau modèle
    'project': 'runs/detect',    # Repertoire du modèle

    'data': 'coco8.yaml',      # Données à utiliser lors de la distillation
    'epochs': 30,                # Nombre d'époques
    'batch': 16,                 # Taille de batchs
    'exist_ok': True,            # Ecrase l'itération précédente du projet si elle existe déjà

    # Note: la majorité des attributs du fine-tuning ordinaire sont également supportés pour la distillation
    # Une liste détaillée de tous les attributs et leurs valeurs par défaut:
    # https://github.com/danielsyahputra/yolo-distiller/blob/a2f004c6227ffb9e3c8fe172c824f96e51c20999/ultralytics/cfg/default.yaml#L89
}

results = student_model.train(**distillation_args)

New https://pypi.org/project/ultralytics/8.3.143 available 😃 Update with 'pip install -U ultralytics'
Ultralytics 8.3.24 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
engine/trainer: task=detect, mode=train, model=yolo11s.pt, data=coco8.yaml, epochs=30, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=runs/detect, name=yolo_distillation, exist_ok=True, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_fram

train: Scanning /content/datasets/coco8/labels/train.cache... 4 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4/4 [00:00<?, ?it/s]

albumentations: Blur(p=0.01, blur_limit=(3, 7)), MedianBlur(p=0.01, blur_limit=(3, 7)), ToGray(p=0.01, method='weighted_average', num_output_channels=3), CLAHE(p=0.01, clip_limit=(1.0, 4.0), tile_grid_size=(8, 8))



/usr/local/lib/python3.11/dist-packages/ultralytics/data/augment.py:1850: UserWarning: Argument(s) 'quality_lower' are not valid for transform ImageCompression
  A.ImageCompression(quality_lower=75, p=0.0),
val: Scanning /content/datasets/coco8/labels/val.cache... 4 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4/4 [00:00<?, ?it/s]


Plotting labels to runs/detect/yolo_distillation/labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.000119, momentum=0.9) with parameter groups 248 weight(decay=0.0), 262 weight(decay=0.0005), 260 bias(decay=0.0)
TensorBoard: model graph visualization added ✅
Image sizes 640 train, 640 val
Using 2 dataloader workers
Logging results to runs/detect/yolo_distillation
Starting training for 30 epochs...

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


...

      30/30      1.95G     0.8067     0.6647      1.224         13        640: 100%|██████████| 1/1 [00:00<00:00,  3.90it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00, 17.28it/s]

                   all          4         17      0.703       0.75      0.825      0.591



30 epochs completed in 0.014 hours.
Optimizer stripped from runs/detect/yolo_distillation/weights/last.pt, 19.3MB
Optimizer stripped from runs/detect/yolo_distillation/weights/best.pt, 19.3MB

Validating runs/detect/yolo_distillation/weights/best.pt...
Ultralytics 8.3.24 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
YOLO11s summary (fused): 238 layers, 9,443,760 parameters, 0 gradients, 21.5 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00, 21.66it/s]


                   all          4         17      0.752      0.833      0.932      0.748
                person          3         10       0.86        0.5      0.781      0.423
                   dog          1          1      0.576          1      0.995      0.895
                 horse          1          2      0.815          1      0.995        0.7
              elephant          1          2      0.749        0.5      0.828      0.582
              umbrella          1          1      0.726          1      0.995      0.995
          potted plant          1          1      0.789          1      0.995      0.895
Speed: 0.2ms preprocess, 4.5ms inference, 0.0ms loss, 1.4ms postprocess per image
Results saved to runs/detect/yolo_distillation


# Exportation du modèle et optimisation d'inférence

In [3]:
# Arguments pour l'exportation du modèle vers un format plus performant
# Plus d'informations: https://docs.ultralytics.com/modes/export/
export_args = {
    'format': 'engine',  # Le format d'export du modèle, dans notre cas on vise à l'exporter vers le .engine de TensorRT
    'imgsz': 640,    # Taille fixe pour les images traitées par le modèle exporté
    'dynamic': False,    # Active le support de taille d'image dynamique (potentiellement plus lent)

    'half': True,    # Active la compression sélective des paramètres du modèle en 16bit (plus rapide mais moins précis)
    'int8': False,   # Active la compression sélective des paramètres du modèle en 8bit (encore plus rapide mais encore moins précis)
    'data': 'coco8-pose.yaml', # Fichier de configuration du dataset à utiliser pour la calibration du modèle compréssé
    'fraction': 0.5, # Fraction du dataset à utiliser pour la calibration

    'simplify': True,    # Simplification du modèle lors de la conversion intermédiare vers ONNX
    'batch': 3,      # Taille de batch supporté du modèle exporté
}

In [11]:
# Chargons notre meilleur modèle

best_model_path = train_args['project']+'/'+train_args['name']+'/weights/best.pt'
best_yolo = YOLO(best_model_path)

# Exportons notre modèle:
# Note: il est conseillé d'exporter le modèle directement sur le système embarqué
# le procédé d'exportation prend en compte la configuration du système pour optimiser les performances
best_yolo.export(**export_args)

WARNING ⚠️ TensorRT requires GPU export, automatically assigning device=0
Ultralytics 8.3.24 🚀 Python-3.11.12 torch-2.6.0+cu124 CUDA:0 (Tesla T4, 15095MiB)
YOLO11s-pose summary (fused): 257 layers, 9,902,940 parameters, 0 gradients, 23.1 GFLOPs

PyTorch: starting from 'runs/pose/yolo_finetune/weights/best.pt' with input shape (3, 3, 640, 640) BCHW and output shape(s) (3, 56, 8400) (19.2 MB)
requirements: Ultralytics requirements ['onnx>=1.12.0', 'onnxslim', 'onnxruntime-gpu'] not found, attempting AutoUpdate...
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.6/17.6 MB 108.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 146.2/146.2 kB 237.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 283.2/283.2 MB 83.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 267.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 290.2 MB/s eta 0:00:00

requirements: AutoUpdate success ✅ 20.9s, installed 3 packages: ['onnx>=1.12.0',

'runs/pose/yolo_finetune/weights/best.engine'